##### Saving words from newspaper titles in textfiles

In [1]:
import json
import requests
from bs4 import BeautifulSoup
import time

In [2]:
import json

# Path to the JSON file
json_file_path = 'cdx_results_2019.json'

# Open and load the JSON file
with open(json_file_path, 'r') as file:
    data = json.load(file)

# List to store the URLs
urls = []

# Loop through the data and extract 'url' values
for entry in data:
    if 'url' in entry:  # Check if 'url' key exists
        urls.append(entry['url'])  # Add the URL to the list

# Open a file to write the results
with open("titles.txt", "w") as file:
    # Loop through each URL
    for url in urls:
        # Remove 'https://' and split the URL at slashes
        parts = url.split('/')
        
        # Extract the last part after the slash, which usually contains the title
        title_with_params = parts[-1]
        
        # Remove any parameters (everything after '?')
        title = title_with_params.split('?')[0]
        
        # Replace hyphens with spaces to improve readability
        formatted_title = title.replace('-', ' ')
        
        # Write the formatted title to the file
        file.write(f"{formatted_title}\n")

print("Titles extracted and written to 'titles.txt'.")

# maybe store urls and words wich belong togethers in a dictionary

Titles extracted and written to 'titles.txt'.


#### Writing a function to extract the text out of the weblink

In [ ]:
import json

# Function to split the URL into words from the title
def split_url_in_words(url):
    # Remove 'https://' and split the URL at slashes
    parts = url.split('/')
    
    # Extract the last part after the slash, which usually contains the title
    title_with_params = parts[-1]
    
    # Remove any parameters (everything after '?')
    title = title_with_params.split('?')[0]
    
    # Replace hyphens with spaces to improve readability
    formatted_title = title.replace('-', ' ')
    
    # Return the split words
    return formatted_title

# Path to the JSON file
json_file_path = 'cdx_results_2019.json'

# Open and load the JSON file
with open(json_file_path, 'r') as file:
    data = json.load(file)

# Empty dictionary to store the URLs as keys and the split title words as values
urls = {}

# Iterate through the JSON data
for entry in data:
    if 'url' in entry:
        #url = entry['url']  # Get the full URL
        #split_title = split_url_in_words(url)  # Split the URL title into words
        #urls[str(entry['url'])] = split_title  # Store the URL as key and split title as value
        urls[str(entry['url'])] = split_url_in_words(entry['url'])

# Writing dictionary to a textfile
with open('urls_titles.json', 'w') as output_file:
    json.dump(urls, output_file, indent=4)

 Trying to scrape only the < title > elements in the links and look up if Chega is written as: 'Chega' or 'CHEGA':

In [ ]:
import json
import requests
from bs4 import BeautifulSoup
import time

# Path to the JSON file
file_name = 'cdx_results_2019.json'

# Open and load the JSON file
with open(file_name, 'r') as file:
    data = json.load(file)

titles = {}

# Loop through URLs; search for the title element in HTML-Script
for v in data:
    url = v['url']
    
    try:
        # Requesting the website and setting a timeout of 10 seconds
        response = requests.get(url, timeout=10, stream=True) # stream=True for downloading data in chunks not everything at once 
        
        # Delay between requests to avoid overloading the server
        time.sleep(1)  # 1-second delay

        # Initialize an empty content variable and stream content chunks
        html_content = b""
        
        # Stream the content until we find the closing </title> tag
        for chunk in response.iter_content(chunk_size=512):
            html_content += chunk
            if b"</title>" in html_content:
                break  # Stop streaming once the <title> tag is found

        # Parse only the partial content with BeautifulSoup
        soup = BeautifulSoup(html_content, "html.parser")

        # Extract the <title> element
        title_tag = soup.find("title")

        # If no <title> tag is found, skip this page, makes program faster
        if not title_tag:
            continue

        # Extract the text from the <title> tag
        title_text = title_tag.get_text()

        # Check for "Chega" or "CHEGA" (case-sensitive check)
        if "Chega" in title_text or "CHEGA" or "Andre Ventura" in title_text:
            titles[url] = title_text  # Store the URL and title in the dictionary

    except requests.exceptions.Timeout:
        print(f"Timeout occurred for URL: {url}")
        continue  # Skip to the next URL if a timeout occurs

    except requests.exceptions.RequestException as e:
        print(f"Request failed for URL: {url} with error: {e}")
        continue  # Skip to the next URL if another error occurs

# Writing the dictionary to a JSON file
with open('titles.json', 'w', encoding='utf-8') as json_file:
    json.dump(titles, json_file, indent=4, ensure_ascii=False)

# Print the results, only for debugging, to remove later
for url, title in titles.items():
    print(url, title)

In [ ]:
# Code in 1st delivery:

import json
import requests
from bs4 import BeautifulSoup
import time

# Path to the JSON file
file_name = 'cdx_results_2019.json'

# Open and load the JSON file
with open(file_name, 'r') as file:
    data = json.load(file)

titles = {}

# Loop through URLs; search for the title element in HTML-Script
counter = 0

for v in data:
    url = v['url']
    print(f'iteration {counter}')
    print(f'link: {url}')
    counter += 1
    
    try:
        # Requesting the website and setting a timeout of 10 seconds
        response = requests.get(url, timeout=10, stream=True) # stream=True for downloading data in chunks not everything at once 
        
        # Delay between requests to avoid overloading the server
        # time.sleep(1)  # 1-second delay; should may be in code if server gets too much requests, for now works fine without delay

        # Initialize an empty content variable and stream content chunks
        html_content = b""
        
        # Stream the content until we find the closing </title> tag
        for chunk in response.iter_content(chunk_size=512):
            html_content += chunk
            if b"</title>" in html_content:
                break  # Stop streaming once the <title> tag is found

        # Parse only the partial content with BeautifulSoup
        soup = BeautifulSoup(html_content, "html.parser") # optional lxml parser

        # Extract the <title> element
        title_tag = soup.find("title")

        # If no <title> tag is found, skip this page, makes program faster
        if not title_tag:
            continue

        # Extract the text from the <title> tag
        title_text = title_tag.get_text()

        # Check for "Chega" or "CHEGA" (case-sensitive check)
        if "Chega" in title_text or "CHEGA" or "Andre Ventura" in title_text:
            print(f'title text "{title_text}" is valid"')
            titles[url] = title_text  # Store the URL and title in the dictionary

    except requests.exceptions.Timeout:
        print(f"Timeout occurred for URL: {url}")
        continue  # Skip to the next URL if a timeout occurs

    except requests.exceptions.RequestException as e:
        print(f"Request failed for URL: {url} with error: {e}")
        continue  # Skip to the next URL if another error occurs

# Writing the dictionary to a JSON file
with open('titles.json', 'w', encoding='utf-8') as json_file:
    json.dump(titles, json_file, indent=4, ensure_ascii=False)

In [ ]:
import pandas as pd

# Debug output:

for url, title in titles.items():
    print(f'{url}: {title}')

print(titles)

#df_titles = pd.DataFrame(data=titles)

In [ ]:
from wordcloud import WordCloud
import matplotlib.pyplot as plt

# Combine all titles into one string
all_titles = ' '.join(titles.values())

# Generate a word cloud
wordcloud = WordCloud(width=800, height=400, background_color='white').generate(all_titles)

# Display the word cloud using matplotlib
plt.figure(figsize=(10, 5))
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis('off')  # No axes for a clean look
plt.show()

In [ ]:
import json
import requests
from bs4 import BeautifulSoup
import time

# Path to the JSON file
file_name = 'cdx_results_2019.json'

# Open and load the JSON file
with open(file_name, 'r') as file:
    data = json.load(file)

titles = {}

# Loop through URLs; search for the title element in HTML-Script
counter = 0

for v in data:
    url = v['url']
    print(f'iteration {counter}')
    print(f'link: {url}')
    counter += 1
    
    try:
        # Requesting the website and setting a timeout of 10 seconds
        response = requests.get(url, timeout=10, stream=True) # stream=True for downloading data in chunks not everything at once 
        
        # Delay between requests to avoid overloading the server
        #time.sleep(1)  # 1-second delay

        # Initialize an empty content variable and stream content chunks
        html_content = b""
        
        # Stream the content until we find the closing </title> tag
        for chunk in response.iter_content(chunk_size=512):
            html_content += chunk
            if b"</title>" in html_content:
                break  # Stop streaming once the <title> tag is found

        # Parse only the partial content with BeautifulSoup
        soup = BeautifulSoup(html_content, "html.parser")

        # Extract the <title> element
        title_tag = soup.find("title")

        # If no <title> tag is found, skip this page, makes program faster
        if not title_tag:
            continue

        # Extract the text from the <title> tag
        title_text = title_tag.get_text()

        # Check for "Chega" or "CHEGA" (case-sensitive check)
        if "Chega" in title_text or "CHEGA" in title_text:
            print(f'title text "{title_text} is valid"')
            titles[url] = title_text  # Store the URL and title in the dictionary

    except requests.exceptions.Timeout:
        print(f"Timeout occurred for URL: {url}")
        continue  # Skip to the next URL if a timeout occurs


    except requests.exceptions.RequestException as e:
        print(f"Request failed for URL: {url} with error: {e}")
        continue  # Skip to the next URL if another error occurs

# Writing the dictionary to a JSON file
with open('titles.json', 'w', encoding='utf-8') as json_file:
    json.dump(titsles, json_file, indent=4, ensure_ascii=False)

In [ ]:
# extracting the text too:

In [4]:
# Path to the JSON file
file_name = 'cdx_results_2022-2024.json'

# Open and load the JSON file
with open(file_name, 'r') as file:
    data = json.load(file)

newspaper_values = {}

# Loop through URLs; search for the title element in HTML-Script
counter = 0
no_title_counter = 0

for v in data:
    url = v['url']
    print(f'iteration {counter}')
    # print(f'link: {url}')
    counter += 1
    
    try:
        # Requesting the website and setting a timeout of 10 seconds
        response = requests.get(url, timeout=10, stream=True) # stream=True for downloading data in chunks not everything at once 
        
        # Delay between requests to avoid overloading the server
        # time.sleep(1)  # 1-second delay; should may be in code if server gets too much requests, for now works fine without delay

        # Initialize an empty content variable and stream content chunks
        html_content = b""
        
        # Stream the content until we find the closing </title> tag
        for chunk in response.iter_content(chunk_size=512):
            html_content += chunk
            # if b"</title>" in html_content:
                # break  # Stop streaming once the <title> tag is found

        # Parse only the partial content with BeautifulSoup
        soup = BeautifulSoup(html_content, "html.parser") # optional lxml parser

        # Extract the <title> element
        title_tag = soup.find("title")
        text_tag = soup.find_all("p")

        # If no <title> tag is found, skip this page, makes program faster
        if not title_tag:
            no_title_counter += 1
            continue

        # Extract title and text from the <title>/<p>-tag
        title_text = title_tag.get_text()

        text_text = ""
        for text in text_tag:
            text_text += text.get_text()

        # Check for "Chega" or "CHEGA" (case-sensitive check)
        if "Chega" in title_text or "CHEGA" in title_text or "Andre Ventura" in title_text:
            print(f'title text "{title_text}" is valid"')
            print(f'Text found in <p> element: {text_text}')
            newspaper_values['url'] = url  # Store the URL and title in the dictionary
            newspaper_values['title'] = title_text 
            newspaper_values['text'] = text_text

    except requests.exceptions.Timeout:
        print(f"Timeout occurred for URL: {url}")
        continue  # Skip to the next URL if a timeout occurs

    except requests.exceptions.RequestException as e:
        print(f"Request failed for URL: {url} with error: {e}")
        continue  # Skip to the next URL if another error occurs

df_newspaper_values = df.DataFrame(data=newspaper_values)

# Writing the dictionary to a JSON file
with open('newspaper_url_infos.json', 'w', encoding='utf-8') as json_file:
    json.dump(titles, json_file, indent=4, ensure_ascii=False)

iteration 0
iteration 1
iteration 2
iteration 3
iteration 4
iteration 5
iteration 6
iteration 7
iteration 8
iteration 9
iteration 10
iteration 11
iteration 12
iteration 13
iteration 14
iteration 15
iteration 16
title text "Imigração: Aceita-se referendo exigido pelo Chega para aprovar o Orçamento? - Perguntas CM - Correio da Manhã" is valid"
Text found in <p> element: A informação do País e do mundo em primeiro lugarNotícias em primeira mão, entrevistas, fotos e vídeos dos seus famososVersão online da revista de fim de semana do jornal Correio da ManhãAs suas notícias acompanhadas ao detalhe.
                    Para usar esta funcionalidade deverá efetuar login. 
                    Caso não esteja registado no site do Correio da Manhã, efetue o seu registo gratuito.
                
iteration 17
iteration 18
iteration 19
iteration 20
iteration 21
title text "Chega e IL: Parlamento exclui voto de mais de 672 mil eleitores - Política - Correio da Manhã" is valid"
Text found in <p> elem

NameError: name 'df' is not defined

#### ToDo: store newspapers with url title and text in a pandas df:

In [3]:
# Eingabedatei mit URLs
file_name = 'cdx_results_2019.json'

# Eingabe-JSON laden
with open(file_name, 'r') as file:
    data = json.load(file)

# Liste, um die Ergebnisse zu sammeln
records = []

# Iteration über die URLs in der Eingabedatei
for index, entry in enumerate(data):
    url = entry['url']
    print(f'Iteration {index + 1}, URL: {url}')
    
    try:
        # Website anfragen
        response = requests.get(url, timeout=10)
        html_content = response.content  # Gesamten Inhalt laden

        # HTML parsen
        soup = BeautifulSoup(html_content, "lxml")

        # <title>-Element und <p>-Tags extrahieren
        title_tag = soup.find("title")
        
        # Prüfen, ob ein <title>-Tag vorhanden ist
        if not title_tag:
            print(f"Kein <title>-Tag gefunden für URL: {url}")
            continue
        
        text_tags = soup.find_all("p")

        # Titeltext extrahieren
        title_text = title_tag.get_text().strip()

        if "Chega" in title_text or "CHEGA" in title_text or "Andre Ventura" in title_text:
            # Text aller <p>-Tags sammeln
            cat_text = "\n".join([p.get_text().strip() for p in text_tags])
            print(f'cat text: {cat_text}')
            # Ergebnis zur Liste hinzufügen
            records.append({
                "URL": url,
                "Title": title_text,
                "Text": cat_text
            })

    except requests.exceptions.Timeout:
        print(f"Timeout bei URL: {url}")
        continue

    except requests.exceptions.RequestException as e:
        print(f"Anfrage fehlgeschlagen für URL: {url} mit Fehler: {e}")
        continue

# DataFrame erstellen und in JSON-Datei speichern
df_newspaper_values = pd.DataFrame(records)
df_newspaper_values.to_json('newspaper_url_infos.json', orient='records', indent=4, force_ascii=False)

# Ausgabe des DataFrames zur Überprüfung

Iteration 1, URL: https://www.cmjornal.pt/boa-vida/amp/capital-do-natal-chega-a-oeiras
Iteration 2, URL: https://www.cmjornal.pt/boa-vida/amp/capital-do-natal-chega-a-oeiras
Iteration 3, URL: https://www.cmjornal.pt/boa-vida/detalhe/capital-do-natal-chega-a-oeiras
Iteration 4, URL: https://www.cmjornal.pt/boa-vida/detalhe/capital-do-natal-chega-a-oeiras
Iteration 5, URL: https://www.cmjornal.pt/boa-vida/detalhe/capital-do-natal-chega-a-oeiras?ref=HP_Africa_BlocoBoaVida&act=0&est=Aberto
Iteration 6, URL: https://www.cmjornal.pt/boa-vida/detalhe/capital-do-natal-chega-a-oeiras?ref=HP_Africa_BlocoBoaVida&act=0&est=Aberto
Iteration 7, URL: https://www.cmjornal.pt/boa-vida/detalhe/capital-do-natal-chega-a-oeiras?ref=HP_BlocoBoaVida&act=0&est=Aberto
Iteration 8, URL: https://www.cmjornal.pt/boa-vida/detalhe/capital-do-natal-chega-a-oeiras?ref=HP_BlocoBoaVida&act=0&est=Aberto
Iteration 9, URL: https://www.cmjornal.pt/boa-vida/detalhe/capital-do-natal-chega-a-oeiras?ref=HP_Africa_BlocoBoaVida


KeyboardInterrupt: 

#### Goals for second submission:

- urls, title and text is stored in a pandas dataframe
- scrape title and text in the dataframe
- clean text from dataframe
- visualize results

##### For today:
Define function to select articles based on the title analysis (from the URL)
- Store the selected URLs in a dataframe with 'url', 'newspaper name', 'title' (joão's part)

Webscrape the selected URLs
- Store the text in the dataframe in an extra column 'article text' (my part)

In [2]:
#### structures of webpages:
# - cmjornal.pt: <div class="texto_container paywall"> # assuming it's the same structure on every cmjornal.pt page
# - dn.pt: hard, watch later
# - expresso.pt: <div class="article content">
# - folhanacional.pt: error?
# - jn.pt: <div class='t-article-content-inner js-selected-and-share-1> search for <p>-elements


In [ ]:
######################################################################################################
# Webscrapping party without checking 'Chega', 'chega' usw, it is already handled in the link checking 
######################################################################################################

# idea: iterating through dataframe, entering every website and search for all <p> elements; concatenate it to a string and add it
#       as a new column in the pd DataFrame